In [1]:
# Imports
import pandas as pd
from ftplib import FTP
import os, sys
import polars as pl
import plotly.express as px

import polars as pl
import polars.selectors as cs
import plotly.express as px
import json
import geopandas
import urllib.request
from urllib.request import urlopen
import numpy as np
import ezregex as er
import plotly.graph_objects as go
import json
import shapely as shp
import geopandas as gpd
import numpy as np
import pyarrow
from polars import col as c


In [2]:
# Load in the main datasets
total_pop_5y_2022 = pl.read_csv('https://www2.census.gov/programs-surveys/acs/summary_file/2022/table-based-SF/data/5YRData/acsdt5y2022-b01003.dat', separator='|')
total_pop_5y_2021 = pl.read_csv('https://www2.census.gov/programs-surveys/acs/summary_file/2021/table-based-SF/data/5YRData/acsdt5y2021-b01003.dat', separator='|')
total_pop_5y_2020 = pl.read_csv('https://www2.census.gov/programs-surveys/acs/summary_file/2020/prototype/5YRData/acsdt5y2020-b01003.dat', separator='|')

In [3]:
# Add what years they each are as a column
total_pop_5y_2022 = total_pop_5y_2022.with_columns(year=pl.lit(2022))
total_pop_5y_2021 = total_pop_5y_2021.with_columns(year=pl.lit(2021))
total_pop_5y_2020 = total_pop_5y_2020.with_columns(year=pl.lit(2020))

In [4]:
total_pop_5y = total_pop_5y_2020.vstack(total_pop_5y_2021).vstack(total_pop_5y_2022)

In [33]:
total_pop_5y.write_parquet('/home/zeke/Data/IdahoPopulation_2020-2022.parquet')

In [5]:
# A code cell to convert shapefiles into geojson (for plotly.chropleth)
# myshpfile = geopandas.read_file('/home/zeke/Data/Shapefiles/tl_2020_us_zcta520/tl_2020_us_zcta520.shp')
# myshpfile.to_file('/home/zeke/Data/Shapefiles/tl_2020_us_zcta520/tl_2020_us_zcta520.geojson', driver='GeoJSON')


In [6]:
# Read the shapefiles
# with open('/home/zeke/Data/Shapefiles/cb_2023_16_tract_500k/cb_2023_16_tract_500k.geojson') as f:
#     tract_geojson = json.load(f)

# with open('/home/zeke/Data/Shapefiles/cb_2023_16_bg_500k/cb_2023_16_bg_500k.geojson') as f:
#     block_group_geojson = json.load(f)

# This is *huge*
# with open('/home/zeke/Data/Shapefiles/tl_2020_us_zcta520/tl_2020_us_zcta520.geojson') as f:
#     zip_geojson_full = json.load(f)

with open('/home/zeke/Data/Shapefiles/2020_zip_ID.geojson') as f:
    zip_geojson_id = json.load(f)

In [7]:
counties = {'16001': "Ada", '16045': "Gem", '16015': "Boise", '16027': 'Canyon'}
clean = (total_pop_5y
    # Use just the 5 year survey data
    # .filter(c('survey') == 'ACS 5 year')
    # Filter just the block groups
    # We just want the tracts
    .filter(c('GEO_ID').str.len_bytes() == 11+9)
    # Remove the useless part of the GEOID
    .select(
        'year',
        GEOID=c('GEO_ID').str.slice(9),
        county=c('GEO_ID').str.slice(9, 5).replace(counties),
        pop='B01003_E001',
        err=c('B01003_M001').replace({-555555555: 1}),
    )
    # Get just the counties we want
    .filter(c('county').is_in(counties.values()))
)
clean

shape: (570, 5)
┌──────┬─────────────┬────────┬──────┬─────┐
│ year ┆ GEOID       ┆ county ┆ pop  ┆ err │
│ ---  ┆ ---         ┆ ---    ┆ ---  ┆ --- │
│ i32  ┆ str         ┆ str    ┆ i64  ┆ i64 │
╞══════╪═════════════╪════════╪══════╪═════╡
│ 2020 ┆ 16001000101 ┆ Ada    ┆ 1273 ┆ 323 │
│ 2020 ┆ 16001000102 ┆ Ada    ┆ 2737 ┆ 473 │
│ 2020 ┆ 16001000201 ┆ Ada    ┆ 3300 ┆ 439 │
│ 2020 ┆ 16001000202 ┆ Ada    ┆ 5782 ┆ 609 │
│ 2020 ┆ 16001000302 ┆ Ada    ┆ 3306 ┆ 444 │
│ …    ┆ …           ┆ …      ┆ …    ┆ …   │
│ 2022 ┆ 16027022400 ┆ Canyon ┆ 4969 ┆ 662 │
│ 2022 ┆ 16045960100 ┆ Gem    ┆ 5555 ┆ 545 │
│ 2022 ┆ 16045960200 ┆ Gem    ┆ 6833 ┆ 567 │
│ 2022 ┆ 16045960301 ┆ Gem    ┆ 4366 ┆ 595 │
│ 2022 ┆ 16045960302 ┆ Gem    ┆ 2496 ┆ 305 │
└──────┴─────────────┴────────┴──────┴─────┘

In [8]:
# Calculate the growth
growth = (clean
    .group_by('GEOID')
    # 2022 comes last, because of how I stacked the dataframes
    .agg(growth=pl.last('pop') - pl.first('pop'))
)
clean = clean.join(growth, on='GEOID', how='left')

In [9]:
# Add the zip column
tract2zip_raw = pl.read_csv('https://www2.census.gov/geo/docs/maps-data/data/rel2020/zcta520/tab20_zcta520_tract20_natl.txt', separator='|')
tract2zip = tract2zip_raw.select(zip='GEOID_ZCTA5_20', GEOID=c('GEOID_TRACT_20').cast(str))
clean = clean.join(tract2zip, on='GEOID', how='left')

In [2]:
tract2zip_raw = pl.read_csv('https://www2.census.gov/geo/docs/maps-data/data/rel2020/zcta520/tab20_zcta520_tract20_natl.txt', separator='|')
tract2zip = tract2zip_raw.select(zip='GEOID_ZCTA5_20', GEOID=c('GEOID_TRACT_20').cast(str))

In [4]:
tract2zip.write_csv('/home/zeke/hello/python/optometrist_graphs/tract2zip.csv')

In [5]:
tract2zip

shape: (171_480, 2)
┌───────┬────────────┐
│ zip   ┆ GEOID      │
│ ---   ┆ ---        │
│ str   ┆ str        │
╞═══════╪════════════╡
│ null  ┆ 1003010100 │
│ null  ┆ 1003010300 │
│ null  ┆ 1003010707 │
│ null  ┆ 1003010710 │
│ null  ┆ 1003990000 │
│ …     ┆ …          │
│ 99923 ┆ 2198000300 │
│ 99925 ┆ 2198000200 │
│ 99926 ┆ 2198940100 │
│ 99927 ┆ 2198000100 │
│ 99929 ┆ 2275000300 │
└───────┴────────────┘

In [ ]:
tract2zip.to_csv('/home/zeke/hello/python/optometrist_graphs/tract2zip.csv')

In [10]:
zips = clean.filter(c('zip').is_not_null())['zip'].to_list()

In [11]:
# zip_geojson['features'][50]['properties']

In [12]:
# Filter out just the zipcodes in Idaho, so it's more managable
zip_geojson_ours = {}
zip_geojson_ours['type'] = zip_geojson_id['type']
zip_geojson_ours['crs'] = zip_geojson_id['crs']
zip_geojson_ours['features'] = [i for i in zip_geojson_id['features'] if i['properties']['GEOID20'] in zips]

In [35]:
with open('/home/zeke/hello/python/optometrist_graphs/zip_codes.geojson', 'w') as f:
    json.dump(zip_geojson_ours, f)

In [26]:
# We calculated the growth, then joined it back, so all the years should have the same growth data
fig = px.choropleth(clean.filter(c('year') == 2022),
    scope='usa',
    color='growth',
    featureidkey='properties.ZCTA5CE20',
    locations='zip',
    hover_data=('zip', 'growth', 'county', 'pop'),
    geojson=zip_geojson_ours,
    title=f'Population Growth in West Idaho Zip Codes from 2020 - 2022',
    color_continuous_scale=px.colors.sequential.PuBu,
    # color_continuous_scale=px.colors.sequential.Blues,
)
fig.update_geos(
    fitbounds="locations",
    visible=False,
    showsubunits=True,
    subunitcolor='black',
)
fig.update_layout(
    autosize=False,
    width=800,
    height=600,
)
fig